# Machine Translation using OpenNMT

# Jamo and Char Tokenization

In [2]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [3]:
!pip install hgtk

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
  Created wheel for hgtk: filename=hgtk-0.1.3-py2.py3-none-any.whl size=6689 sha256=c79e1449aa15b61035cead5f6ce27dcce6f4dc168f720c8444872605bbc5f22e
  Stored in directory: /home/ubuntu/.cache/pip/wheels/96/10/4b/0887dcaf5e0b0d26b807fef3497703fea2c44a76f91d198bd3
Successfully built hgtk


In [1]:
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt.code -s 32000

In [4]:
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-morph.txt
!python OpenNMT-py/tools/apply_morph_ko.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-morph.txt

In [2]:
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-valid.txt -o OpenNMT-py/Data/tgt-val-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-test.txt -o OpenNMT-py/Data/tgt-test-bpe.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [3]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-morph.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-morph.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/morph2bpe/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-09 16:26:38,041 INFO] Extracting features...
[2020-12-09 16:26:38,042 INFO]  * number of source features: 0.
[2020-12-09 16:26:38,042 INFO]  * number of target features: 0.
[2020-12-09 16:26:38,042 INFO] Building `Fields` object...
[2020-12-09 16:26:38,042 INFO] Building & saving training data...
[2020-12-09 16:26:41,799 INFO] Building shard 0.
[2020-12-09 16:27:27,339 INFO]  * saving 0th train data shard to OpenNMT-py/Data/morph2bpe/demo.train.0.pt.
[2020-12-09 16:28:03,810 INFO]  * tgt vocab size: 32485.
[2020-12-09 16:28:06,762 INFO]  * src vocab size: 739301.
[2020-12-09 16:28:11,214 INFO] Building & saving validation data...
[2020-12-09 16:28:15,182 INFO] Building shard 0.
[2020-12-09 16:28:15,709 INFO]  * saving 0th valid data shard to OpenNMT-py/Data/morph2bpe/demo.valid.0.pt.


!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [4]:
!nvidia-smi

Wed Dec  9 16:28:17 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   26C    P8    12W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [6]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/morph2bpe/demo -save_model OpenNMT-py/Data/morph2bpe/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 10000 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/morph2bpe'

[2020-12-09 16:38:12,910 INFO]  * src vocab size = 739301
[2020-12-09 16:38:12,910 INFO]  * tgt vocab size = 32485
[2020-12-09 16:38:12,910 INFO] Building model...
[2020-12-09 16:38:31,710 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(739301, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_fe

[2020-12-09 16:38:31,950 INFO] Starting training on GPU: [0]
[2020-12-09 16:38:31,950 INFO] Start training loop and validate every 1000 steps...
[2020-12-09 16:38:31,950 INFO] Loading dataset from OpenNMT-py/Data/morph2bpe/demo.train.0.pt
[2020-12-09 16:38:59,675 INFO] number of examples: 739263
[2020-12-09 16:39:30,172 INFO] Step 50/50000; acc:   2.55; ppl: 7720.71; xent: 8.95; lr: 0.00001; 232/7016 tok/s;     58 sec
[2020-12-09 16:39:53,781 INFO] Step 100/50000; acc:   6.25; ppl: 5800.82; xent: 8.67; lr: 0.00001; 567/17294 tok/s;     82 sec
[2020-12-09 16:40:17,424 INFO] Step 150/50000; acc:   6.17; ppl: 4307.71; xent: 8.37; lr: 0.00002; 599/17253 tok/s;    105 sec
[2020-12-09 16:40:41,123 INFO] Step 200/50000; acc:   6.25; ppl: 2944.11; xent: 7.99; lr: 0.00002; 556/17228 tok/s;    129 sec
[2020-12-09 16:41:05,082 INFO] Step 250/50000; acc:   6.23; ppl: 1952.45; xent: 7.58; lr: 0.00003; 535/17020 tok/s;    153 sec
[2020-12-09 16:41:28,832 INFO] Step 300/50000; acc:   6.29; ppl: 1334.

[2020-12-09 17:03:08,240 INFO] Step 2900/50000; acc:  25.56; ppl: 74.51; xent: 4.31; lr: 0.00036; 528/17171 tok/s;   1476 sec
[2020-12-09 17:03:31,785 INFO] Step 2950/50000; acc:  25.52; ppl: 74.77; xent: 4.31; lr: 0.00036; 590/17325 tok/s;   1500 sec
[2020-12-09 17:03:55,379 INFO] Step 3000/50000; acc:  25.69; ppl: 73.02; xent: 4.29; lr: 0.00037; 590/17307 tok/s;   1523 sec
[2020-12-09 17:03:55,381 INFO] Loading dataset from OpenNMT-py/Data/morph2bpe/demo.valid.0.pt
[2020-12-09 17:03:55,625 INFO] number of examples: 8014
[2020-12-09 17:04:03,110 INFO] Validation perplexity: 118.359
[2020-12-09 17:04:03,110 INFO] Validation accuracy: 26.4415
[2020-12-09 17:04:26,780 INFO] Step 3050/50000; acc:  25.85; ppl: 71.64; xent: 4.27; lr: 0.00038; 411/12999 tok/s;   1555 sec
[2020-12-09 17:04:50,410 INFO] Step 3100/50000; acc:  25.92; ppl: 71.02; xent: 4.26; lr: 0.00038; 545/17251 tok/s;   1578 sec
[2020-12-09 17:05:14,412 INFO] Step 3150/50000; acc:  26.04; ppl: 69.09; xent: 4.24; lr: 0.00039; 

[2020-12-09 17:27:17,716 INFO] Step 5800/50000; acc:  30.17; ppl: 43.88; xent: 3.78; lr: 0.00072; 592/17169 tok/s;   2926 sec
[2020-12-09 17:27:41,725 INFO] Step 5850/50000; acc:  30.35; ppl: 42.94; xent: 3.76; lr: 0.00072; 560/17008 tok/s;   2950 sec
[2020-12-09 17:28:05,614 INFO] Step 5900/50000; acc:  30.39; ppl: 42.90; xent: 3.76; lr: 0.00073; 536/17068 tok/s;   2974 sec
[2020-12-09 17:28:29,379 INFO] Step 5950/50000; acc:  30.65; ppl: 42.11; xent: 3.74; lr: 0.00074; 541/17170 tok/s;   2997 sec
[2020-12-09 17:28:53,220 INFO] Step 6000/50000; acc:  30.70; ppl: 41.73; xent: 3.73; lr: 0.00074; 529/17121 tok/s;   3021 sec
[2020-12-09 17:28:53,222 INFO] Loading dataset from OpenNMT-py/Data/morph2bpe/demo.valid.0.pt
[2020-12-09 17:28:53,483 INFO] number of examples: 8014
[2020-12-09 17:29:01,032 INFO] Validation perplexity: 77.1844
[2020-12-09 17:29:01,032 INFO] Validation accuracy: 29.3574
[2020-12-09 17:29:24,831 INFO] Step 6050/50000; acc:  30.74; ppl: 41.76; xent: 3.73; lr: 0.00075; 

[2020-12-09 17:51:25,285 INFO] Step 8700/50000; acc:  34.25; ppl: 30.59; xent: 3.42; lr: 0.00095; 537/17143 tok/s;   4373 sec
[2020-12-09 17:51:49,158 INFO] Step 8750/50000; acc:  34.46; ppl: 30.13; xent: 3.41; lr: 0.00094; 539/17078 tok/s;   4397 sec
[2020-12-09 17:52:12,953 INFO] Step 8800/50000; acc:  34.88; ppl: 29.02; xent: 3.37; lr: 0.00094; 534/17155 tok/s;   4421 sec
[2020-12-09 17:52:36,887 INFO] Step 8850/50000; acc:  34.84; ppl: 29.23; xent: 3.38; lr: 0.00094; 535/17045 tok/s;   4445 sec
[2020-12-09 17:53:00,838 INFO] Step 8900/50000; acc:  35.18; ppl: 28.63; xent: 3.35; lr: 0.00094; 538/17045 tok/s;   4469 sec
[2020-12-09 17:53:24,502 INFO] Step 8950/50000; acc:  35.12; ppl: 28.55; xent: 3.35; lr: 0.00093; 553/17252 tok/s;   4493 sec
[2020-12-09 17:53:48,121 INFO] Step 9000/50000; acc:  35.27; ppl: 28.13; xent: 3.34; lr: 0.00093; 562/17290 tok/s;   4516 sec
[2020-12-09 17:53:48,123 INFO] Loading dataset from OpenNMT-py/Data/morph2bpe/demo.valid.0.pt
[2020-12-09 17:53:48,371

...

[2020-12-09 21:53:08,292 INFO] Step 37350/50000; acc:  63.54; ppl:  4.87; xent: 1.58; lr: 0.00046; 550/17211 tok/s;  18876 sec
[2020-12-09 21:53:32,112 INFO] Step 37400/50000; acc:  63.64; ppl:  4.87; xent: 1.58; lr: 0.00046; 538/17136 tok/s;  18900 sec
[2020-12-09 21:53:55,663 INFO] Step 37450/50000; acc:  64.48; ppl:  4.67; xent: 1.54; lr: 0.00046; 563/17335 tok/s;  18924 sec
[2020-12-09 21:54:19,533 INFO] Step 37500/50000; acc:  63.16; ppl:  4.94; xent: 1.60; lr: 0.00046; 527/17098 tok/s;  18948 sec
[2020-12-09 21:54:43,149 INFO] Step 37550/50000; acc:  63.71; ppl:  4.79; xent: 1.57; lr: 0.00046; 545/17274 tok/s;  18971 sec
[2020-12-09 21:55:06,825 INFO] Step 37600/50000; acc:  63.55; ppl:  4.83; xent: 1.57; lr: 0.00046; 540/17245 tok/s;  18995 sec
[2020-12-09 21:55:30,493 INFO] Step 37650/50000; acc:  63.91; ppl:  4.80; xent: 1.57; lr: 0.00046; 538/17244 tok/s;  19019 sec
[2020-12-09 21:55:54,041 INFO] Step 37700/50000; acc:  65.48; ppl:  4.50; xent: 1.50; lr: 0.00046; 589/17337 to

[2020-12-09 22:17:43,406 INFO] Step 40200/50000; acc:  65.19; ppl:  4.52; xent: 1.51; lr: 0.00044; 556/17054 tok/s;  20351 sec
[2020-12-09 22:18:07,301 INFO] Step 40250/50000; acc:  64.89; ppl:  4.56; xent: 1.52; lr: 0.00044; 538/17087 tok/s;  20375 sec
[2020-12-09 22:18:31,159 INFO] Step 40300/50000; acc:  65.49; ppl:  4.47; xent: 1.50; lr: 0.00044; 550/17109 tok/s;  20399 sec
[2020-12-09 22:18:54,905 INFO] Step 40350/50000; acc:  64.46; ppl:  4.62; xent: 1.53; lr: 0.00044; 535/17187 tok/s;  20423 sec
[2020-12-09 22:19:18,674 INFO] Step 40400/50000; acc:  64.85; ppl:  4.56; xent: 1.52; lr: 0.00044; 539/17165 tok/s;  20447 sec
[2020-12-09 22:19:42,459 INFO] Step 40450/50000; acc:  64.28; ppl:  4.67; xent: 1.54; lr: 0.00044; 525/17165 tok/s;  20471 sec
[2020-12-09 22:20:06,027 INFO] Step 40500/50000; acc:  65.76; ppl:  4.41; xent: 1.48; lr: 0.00044; 565/17319 tok/s;  20494 sec
[2020-12-09 22:20:29,567 INFO] Step 40550/50000; acc:  65.51; ppl:  4.46; xent: 1.50; lr: 0.00044; 557/17330 to

[2020-12-09 22:41:31,326 INFO] Step 43050/50000; acc:  65.77; ppl:  4.38; xent: 1.48; lr: 0.00043; 411/13006 tok/s;  21779 sec
[2020-12-09 22:41:54,993 INFO] Step 43100/50000; acc:  66.41; ppl:  4.27; xent: 1.45; lr: 0.00043; 554/17248 tok/s;  21803 sec
[2020-12-09 22:42:18,866 INFO] Step 43150/50000; acc:  65.40; ppl:  4.47; xent: 1.50; lr: 0.00043; 531/17099 tok/s;  21827 sec
[2020-12-09 22:42:42,583 INFO] Step 43200/50000; acc:  65.75; ppl:  4.36; xent: 1.47; lr: 0.00043; 528/17198 tok/s;  21851 sec
[2020-12-09 22:43:06,331 INFO] Step 43250/50000; acc:  65.63; ppl:  4.40; xent: 1.48; lr: 0.00043; 540/17195 tok/s;  21874 sec
[2020-12-09 22:43:30,227 INFO] Step 43300/50000; acc:  65.69; ppl:  4.40; xent: 1.48; lr: 0.00042; 533/17077 tok/s;  21898 sec
[2020-12-09 22:43:53,915 INFO] Step 43350/50000; acc:  67.95; ppl:  4.02; xent: 1.39; lr: 0.00042; 599/17238 tok/s;  21922 sec
[2020-12-09 22:44:17,786 INFO] Step 43400/50000; acc:  65.69; ppl:  4.38; xent: 1.48; lr: 0.00042; 528/17091 to

[2020-12-09 23:06:00,009 INFO] number of examples: 8014
[2020-12-09 23:06:07,456 INFO] Validation perplexity: 233.295
[2020-12-09 23:06:07,456 INFO] Validation accuracy: 25.7827
[2020-12-09 23:06:31,295 INFO] Step 46050/50000; acc:  67.03; ppl:  4.14; xent: 1.42; lr: 0.00041; 404/12770 tok/s;  23279 sec
[2020-12-09 23:06:55,106 INFO] Step 46100/50000; acc:  66.23; ppl:  4.27; xent: 1.45; lr: 0.00041; 530/17146 tok/s;  23303 sec
[2020-12-09 23:07:18,777 INFO] Step 46150/50000; acc:  67.57; ppl:  4.05; xent: 1.40; lr: 0.00041; 565/17244 tok/s;  23327 sec
[2020-12-09 23:07:42,670 INFO] Step 46200/50000; acc:  67.11; ppl:  4.13; xent: 1.42; lr: 0.00041; 545/17080 tok/s;  23351 sec
[2020-12-09 23:08:06,639 INFO] Step 46250/50000; acc:  67.36; ppl:  4.10; xent: 1.41; lr: 0.00041; 552/17028 tok/s;  23375 sec
[2020-12-09 23:08:30,592 INFO] Step 46300/50000; acc:  66.22; ppl:  4.26; xent: 1.45; lr: 0.00041; 524/17046 tok/s;  23399 sec
[2020-12-09 23:08:54,530 INFO] Step 46350/50000; acc:  66.48

[2020-12-09 23:30:41,066 INFO] Step 48950/50000; acc:  67.20; ppl:  4.10; xent: 1.41; lr: 0.00040; 529/17072 tok/s;  24729 sec
[2020-12-09 23:31:04,871 INFO] Step 49000/50000; acc:  69.43; ppl:  3.76; xent: 1.32; lr: 0.00040; 588/17151 tok/s;  24753 sec
[2020-12-09 23:31:04,873 INFO] Loading dataset from OpenNMT-py/Data/morph2bpe/demo.valid.0.pt
[2020-12-09 23:31:05,152 INFO] number of examples: 8014
[2020-12-09 23:31:12,676 INFO] Validation perplexity: 271.657
[2020-12-09 23:31:12,676 INFO] Validation accuracy: 26.2823
[2020-12-09 23:31:36,485 INFO] Step 49050/50000; acc:  67.46; ppl:  4.04; xent: 1.40; lr: 0.00040; 399/12906 tok/s;  24785 sec
[2020-12-09 23:32:00,308 INFO] Step 49100/50000; acc:  67.66; ppl:  4.02; xent: 1.39; lr: 0.00040; 542/17136 tok/s;  24808 sec
[2020-12-09 23:32:24,191 INFO] Step 49150/50000; acc:  67.15; ppl:  4.10; xent: 1.41; lr: 0.00040; 528/17099 tok/s;  24832 sec
[2020-12-09 23:32:48,082 INFO] Step 49200/50000; acc:  67.76; ppl:  3.98; xent: 1.38; lr: 0.0

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [14]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/morph2bpe/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-morph.txt -output OpenNMT-py/Data/morph2bpe/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 17:33:43,051 INFO] Translating shard 0.
[2020-12-11 17:33:43,836 INFO] 
SENT 1: ['"ᴥ경찰ᴥ의ᴥ설명ᴥ을ᴥ보면ᴥ,ᴥ손님ᴥ으로ᴥ피시방ᴥ을ᴥ찾은ᴥ김씨ᴥ는ᴥ다른ᴥ손님ᴥ이ᴥ남긴ᴥ음식물ᴥ을ᴥ자리ᴥ에서ᴥ치워ᴥ달라ᴥ는ᴥ요구ᴥ를ᴥ하다ᴥ신씨ᴥ와ᴥ말다툼ᴥ을ᴥ했다고ᴥ한다ᴥ."ᴥ']
PRED 1: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:43,836 INFO] 
SENT 2: ['잠실ᴥ여자ᴥ고등학교ᴥ(ᴥ교장ᴥ김인ᴥ봉ᴥ)ᴥ는ᴥ실력ᴥ과ᴥ인성ᴥ을ᴥ갖춘ᴥ인재ᴥ를ᴥ기른다는ᴥ지향ᴥ점ᴥ을ᴥ가지ᴥ고ᴥ교사ᴥ와ᴥ학생ᴥ이ᴥ‘ᴥ신뢰ᴥ의ᴥ팀ᴥ플레이ᴥ’ᴥ를ᴥ통해ᴥ진로ᴥ진학ᴥ프로그램ᴥ을ᴥ업그레이드ᴥ해ᴥ나가고ᴥ있다ᴥ.ᴥ']
PRED 2: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the estab

[2020-12-11 17:33:44,437 INFO] 
SENT 31: ['"ᴥ단독ᴥ콘서트ᴥ무대ᴥ가ᴥ아닌ᴥ,ᴥ주ᴥ시청ᴥ층ᴥ이ᴥ청소년ᴥ들ᴥ인ᴥ시상식ᴥ무대ᴥ였다는ᴥ점ᴥ에서ᴥ화사ᴥ의ᴥ의상ᴥ선택ᴥ에는ᴥ아쉬움ᴥ이ᴥ남는다ᴥ."ᴥ']
PRED 31: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:44,438 INFO] 
SENT 32: ['"ᴥ추가ᴥ취업ᴥ희망ᴥ자ᴥ에다ᴥ구직ᴥ단념ᴥ자ᴥ,ᴥ취업ᴥ준비ᴥ자ᴥ등ᴥ을ᴥ합친ᴥ청년ᴥ층ᴥ의ᴥ잠재ᴥ실업률ᴥ은ᴥ23%ᴥ에ᴥ달해ᴥ청년ᴥ4ᴥ명ᴥ가운데ᴥ한ᴥ명ᴥ이ᴥ실질ᴥ적ᴥ인ᴥ실업ᴥ상태ᴥ에ᴥ놓여ᴥ있는ᴥ상황ᴥ이다ᴥ."ᴥ']
PRED 32: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:44,4

[2020-12-11 17:33:45,037 INFO] 
SENT 61: ['이ᴥ와ᴥ달리ᴥ우기ᴥ에는ᴥ목초ᴥ가ᴥ무성ᴥ해ᴥ구충제ᴥ와ᴥ항생제ᴥ의ᴥ수요ᴥ가ᴥ높다ᴥ.ᴥ']
PRED 61: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:45,038 INFO] 
SENT 62: ['대전ᴥ지역ᴥ경제ᴥ가ᴥ흔들리고ᴥ있다는ᴥ통계ᴥ가ᴥ지난해ᴥ부터ᴥ연ᴥ이ᴥ어ᴥ나오고ᴥ있다ᴥ.ᴥ']
PRED 62: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:45,038 INFO] 
SENT 63: ['"ᴥ남ᴥ측ᴥ에서는ᴥ조용ᴥ근ᴥ육군ᴥ대령ᴥ과ᴥ관련ᴥ실무ᴥ담당ᴥ관ᴥ등ᴥ총ᴥ4ᴥ명ᴥ이ᴥ,ᴥ북ᴥ측ᴥ에서는ᴥ엄창남ᴥ육군ᴥ대좌ᴥ와ᴥ관련ᴥ실무ᴥ담당ᴥ관ᴥ등ᴥ

[2020-12-11 17:33:45,638 INFO] 
SENT 91: ['"ᴥ손석희ᴥJTBCᴥ대표이사ᴥ로부터ᴥ폭행ᴥ을ᴥ당했다고ᴥ주장ᴥ하는ᴥ프리랜서ᴥ기자ᴥ가ᴥ손ᴥ대표ᴥ를ᴥ협박ᴥ,ᴥ명예훼손ᴥ혐의ᴥ등ᴥ으로ᴥ검찰ᴥ에ᴥ추가ᴥ고소했다ᴥ."ᴥ']
PRED 91: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:45,639 INFO] 
SENT 92: ['경찰ᴥ은ᴥ신도ᴥ들ᴥ의ᴥ휴대전화ᴥ전원ᴥ을ᴥ끄도록ᴥ하고ᴥ제출ᴥ받은ᴥ뒤ᴥ어린이ᴥ들ᴥ을ᴥ포함ᴥ한ᴥ신도ᴥ들ᴥ의ᴥ개인ᴥ신원ᴥ을ᴥ일일이ᴥ확인ᴥ하고ᴥ기록ᴥ했다ᴥ.ᴥ']
PRED 92: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:45,639 INFO] 
SENT 93: ['"

[2020-12-11 17:33:46,238 INFO] 
SENT 121: ['그ᴥ과정ᴥ에서ᴥ가장ᴥ중시ᴥ하는ᴥ것ᴥ은ᴥ만화ᴥ의ᴥ특별한ᴥ예술ᴥ성ᴥ에ᴥ만화가ᴥ뿐ᴥ아니라ᴥ모든ᴥ국민ᴥ이ᴥ함께ᴥ참여ᴥ할ᴥ수ᴥ있도록ᴥ하는ᴥ것ᴥ이다ᴥ.ᴥ']
PRED 121: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:46,239 INFO] 
SENT 122: ['"ᴥ부산ᴥ과ᴥ대구ᴥ도ᴥ각각ᴥ76%ᴥ와ᴥ72.9%ᴥ로ᴥ높은ᴥ반면ᴥ,ᴥ세종ᴥ은ᴥ20.0%ᴥ로ᴥ외지ᴥ인ᴥ의ᴥ토지ᴥ소유ᴥ비중ᴥ이ᴥ높은ᴥ것ᴥ으로ᴥ나타났다ᴥ."ᴥ']
PRED 122: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:33:46,239 INFO] 
SENT 123: ['"ᴥ무

...

[2020-12-11 17:36:23,681 INFO] 
SENT 7891: ['그중ᴥ하나ᴥ가ᴥ도시ᴥ계획ᴥ을ᴥ통한ᴥ공동체ᴥ조성ᴥ과ᴥ공유ᴥ가치ᴥ실현ᴥ이다ᴥ.ᴥ']
PRED 7891: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:23,681 INFO] 
SENT 7892: ['모든ᴥ멤버ᴥ가ᴥ10ᴥ대로ᴥ구성ᴥ된ᴥ6ᴥ인조ᴥ그룹ᴥ‘ᴥ더ᴥ이스트ᴥ라이트ᴥ’ᴥ폭행ᴥ사건ᴥ의ᴥ철저한ᴥ수사ᴥ를ᴥ촉구ᴥ하는ᴥ국민ᴥ청원ᴥ동의ᴥ수가ᴥ청와대ᴥ답변ᴥ기준ᴥ인ᴥ20만ᴥ명을ᴥ넘어섰다ᴥ.ᴥ']
PRED 7892: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:23,682 INFO] 
SENT 7893: ['점유ᴥ율ᴥ1ᴥ위인ᴥ신라면ᴥ이ᴥ이

[2020-12-11 17:36:24,301 INFO] 
SENT 7921: ['권용수ᴥ주ᴥ우즈베키스탄ᴥ대사ᴥ는ᴥ“ᴥ스마트ᴥ미터ᴥ프로젝트ᴥ의ᴥ성공ᴥ추진ᴥ을ᴥ바탕ᴥ으로ᴥKTᴥ의ᴥ우즈벡ᴥ사업ᴥ이ᴥ다양한ᴥICTᴥ분야ᴥ로ᴥ확대ᴥ돼ᴥ나가기를ᴥ바란다ᴥ”ᴥ고ᴥ밝혔다ᴥ.ᴥ']
PRED 7921: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:24,302 INFO] 
SENT 7922: ['펑샨샨ᴥ의ᴥ뒤ᴥ를ᴥ이을ᴥ중국ᴥ여자ᴥ골프ᴥ의ᴥ미래ᴥ로ᴥ불리는ᴥ수ᴥ이ᴥ샹ᴥ은ᴥ특히ᴥ쇼트ᴥ게임ᴥ능력ᴥ이ᴥ뛰나다는ᴥ평가ᴥ를ᴥ받는다ᴥ.ᴥ']
PRED 7922: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:24,302 INFO] 
SENT

[2020-12-11 17:36:24,903 INFO] 
SENT 7951: ['카타르ᴥ는ᴥ4ᴥ경기ᴥ서ᴥ10ᴥ골ᴥ을ᴥ허용ᴥ했을ᴥ정도ᴥ로ᴥ수비ᴥ가ᴥ약한ᴥ팀ᴥ이기ᴥ때문ᴥ에ᴥ정상ᴥ적ᴥ으로ᴥ상대ᴥ하면ᴥ충분히ᴥ이길ᴥ수ᴥ있는ᴥ상대ᴥ다ᴥ.ᴥ']
PRED 7951: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:24,904 INFO] 
SENT 7952: ['대상ᴥ㈜ᴥ에서ᴥ제조ᴥ한ᴥ청정ᴥ원ᴥ‘ᴥ런ᴥ천ᴥ미트ᴥ’ᴥ의ᴥ일부ᴥ제품ᴥ에서ᴥ세균ᴥ이ᴥ검ᴥ출ᴥ돼ᴥ식품의약품안전처ᴥ로부터ᴥ판매ᴥ중단ᴥ및ᴥ회수조치ᴥ판정ᴥ을ᴥ받았다ᴥ.ᴥ']
PRED 7952: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:24,904 INFO] 
SENT

[2020-12-11 17:36:25,505 INFO] 
SENT 7981: ['"ᴥ근대ᴥ건축물ᴥ기록ᴥ보존ᴥ사업ᴥ은ᴥ지난ᴥ2010년ᴥ부터ᴥ광주시ᴥ가ᴥ추진ᴥ하고ᴥ있는ᴥ사업ᴥ으로ᴥ,ᴥ그동안ᴥ사업ᴥ대상ᴥ건물ᴥ주의ᴥ비ᴥ협조ᴥ와ᴥ건축물ᴥ산재ᴥ로ᴥ사업ᴥ추진ᴥ에ᴥ적지ᴥ않은ᴥ어려움ᴥ을ᴥ겪었다ᴥ."ᴥ']
PRED 7981: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:25,505 INFO] 
SENT 7982: ['보도ᴥ에ᴥ따르면ᴥ방ᴥ전ᴥ대표ᴥ주변인ᴥ들ᴥ은ᴥ방ᴥ전ᴥ대표ᴥ가ᴥ장ᴥ씨ᴥ와ᴥ2008년ᴥ∼ᴥ2009년ᴥ에ᴥ잠시ᴥ동안ᴥ자주ᴥ만나는ᴥ사이였으며ᴥ방ᴥ대표ᴥ가ᴥ장ᴥ씨ᴥ를ᴥ언급ᴥ하기도ᴥ했다고ᴥ진술ᴥ했다ᴥ.ᴥ']
PRED 7982: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SC

[2020-12-11 17:36:26,001 INFO] 
SENT 8011: ['다만ᴥ북미ᴥ가ᴥ공동ᴥ유해ᴥ발굴ᴥ사업ᴥ에ᴥ합의ᴥ한다면ᴥ미국ᴥ장비ᴥ의ᴥ대북ᴥ반입ᴥ과ᴥ발굴ᴥ비용ᴥ지불ᴥ등ᴥ을ᴥ위ᴥ한ᴥ대북ᴥ제재ᴥ예외ᴥ인정이ᴥ필요하다ᴥ.ᴥ']
PRED 8011: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:26,001 INFO] 
SENT 8012: ['출산ᴥ과ᴥ육아ᴥ에ᴥ대한ᴥ부담ᴥ이ᴥ부모ᴥ에게ᴥ지나치게ᴥ쏠리는ᴥ환경ᴥ을ᴥ개선ᴥ하지ᴥ않으면ᴥ저출산ᴥ문제ᴥ를ᴥ해결ᴥ하는ᴥ건ᴥ요원하다ᴥ.ᴥ']
PRED 8012: "The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""M@@ ir@@ ae Asset Daewoo Securities Per@@ f@@ ect E@@ valu@@ ation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."
PRED SCORE: -0.0715

[2020-12-11 17:36:26,002 INFO] 
SENT 8013: ['여기ᴥ국내ᴥ론


# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [19]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/morph2bpe/pred_50k.txt

# Post-processing

In [4]:
# f = open('OpenNMT-py/Data/tgt-test-char.txt', 'r', encoding='utf-8')
# txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

# with open("OpenNMT-py/Data/tgt-test-char1.txt", "w") as f:
#     f.write(txt)
    
f = open('OpenNMT-py/Data/tgt-test.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'"according to descriptions by the police, mr. kim, who visited the pc-bang as a guest, had an argument with mr. shin while demanding that food left by other guests be cleared from his seat."\n"as jamsil girls\' high school (principal kim in-bong) is aiming to cultivate talents and good personality, the teachers and students are upgrading their career path programs through the ""team-play of trust""."\nformer lawmaker kim will lose both his right to vote and his right to run for 5 years if a fine of 1 million won or more is confirmed.\n"the working environment of daejeon industrial park in daedeok-gu, daejeon will be improved."\n"around 90t of reinforcement facilities were lost due to high waves at the dongbang breakwater construction site in wimi port, namwon-eup, seogwipo-si, and a 100m median strip fell in the area of nohyeong rotary - samsung service center in jeju."\nit is a program to make students value physical education and art.\n"the us department of justice prosecuted assang

In [20]:
# f = open('OpenNMT-py/Data/morph2morph/pred.txt', 'r', encoding='utf-8')
# txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

# with open("OpenNMT-py/Data/morph2morph/pred1.txt", "w") as f:
#     f.write(txt)

f = open('OpenNMT-py/Data/morph2bpe/pred_50k.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'"The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""Mirae Asset Daewoo Securities Perfect Evaluation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."\n"The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""Mirae Asset Daewoo Securities Perfect Evaluation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."\n"The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of ""Mirae Asset Daewoo Securities Perfect Evaluation"" at the National Assembly in Yeouido, Seoul, to commemorate the 100th anniversary of the March 1 Movement and the establishment of the corporation."\n"The Seoul Metropolitan Government said on the 26th that it will hold a large-scale exhibition of "

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [21]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test.txt < OpenNMT-py/Data/morph2bpe/pred_50k.txt

BLEU = 0.31, 13.2/1.4/0.1/0.0 (BP=1.000, ratio=1.587, hyp_len=360636, ref_len=227303)
